# 動的ネットワークの生成

In [30]:
import plotly.graph_objects as go
import networkx as nx
import numpy as np

In [31]:
# 可視化関数の構築
def visualize_network(graph):
    """
    ネットワークデータを可視化する関数。

    Parameters:
        graph (networkx.Graph): ネットワークグラフ (networkxオブジェクト)
    """
    # ノード位置を計算
    pos = nx.spring_layout(graph, seed=42)

    # エッジデータの取得
    edge_x = []
    edge_y = []
    for edge in graph.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x.extend([x0, x1, None])
        edge_y.extend([y0, y1, None])

    # エッジの描画データ
    edge_trace = go.Scatter(
        x=edge_x,
        y=edge_y,
        line=dict(width=1, color='#888'),
        hoverinfo='none',
        mode='lines'
    )

    # ノードデータの取得
    node_x = []
    node_y = []
    node_text = []
    for node in graph.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)
        node_text.append(f"Node {node}")

    # ノードの描画データ
    node_trace = go.Scatter(
        x=node_x,
        y=node_y,
        mode='markers+text',
        text=node_text,
        textposition='top center',
        marker=dict(
            size=5,
            color='skyblue',
            line=dict(width=2, color='darkblue')
        ),
        hoverinfo='text'
    )

    # グラフの描画
    fig = go.Figure(data=[edge_trace, node_trace],
                    layout=go.Layout(
                        title='Interactive Network Graph',
                        title_x=0.5,
                        showlegend=False,
                        hovermode='closest',
                        margin=dict(b=0, l=0, r=0, t=40),
                        xaxis=dict(showgrid=False, zeroline=False),
                        yaxis=dict(showgrid=False, zeroline=False)
                    ))
    fig.show()

In [32]:
def generate_network_data(num_nodes=10, edge_prob=0.3, seed=42):
    """
    ネットワークデータを生成する関数。

    Parameters:
        num_nodes (int): ノード数
        edge_prob (float): エッジが生成される確率
        seed (int): 乱数のシード値

    Returns:
        networkx.Graph: 生成されたネットワークグラフ
    """
    np.random.seed(seed)
    graph = nx.erdos_renyi_graph(n=num_nodes, p=edge_prob, seed=seed)
    return graph

# データ生成と可視化
G = generate_network_data(num_nodes=100, edge_prob=0.2)  # 15ノード、エッジ確率0.2のランダムグラフを生成
visualize_network(G)  # 可視化

## 動的ネットワークの生成

In [33]:
import plotly.graph_objects as go
import networkx as nx
import numpy as np

# 動的ネットワーク生成
def generate_dynamic_network(num_nodes=10, steps=10, seed=42):
    """
    動的ネットワークデータを生成する関数。
    初期状態は1つのクラスタ、最終状態では2つのクラスタに分離。

    Parameters:
        num_nodes (int): ノード数
        steps (int): 状態遷移の補完ステップ数
        seed (int): 乱数シード

    Returns:
        list of networkx.Graph: 各ステップのグラフ
    """
    np.random.seed(seed)
    graphs = []
    
    # 初期状態：すべてのノードが1つのクラスタ
    G_init = nx.Graph()
    G_init.add_nodes_from(range(num_nodes))
    for i in range(num_nodes):
        for j in range(i + 1, num_nodes):
            G_init.add_edge(i, j)
    graphs.append(G_init)

    # 最終状態：ノードが2つのクラスタに分かれる
    cluster1 = range(num_nodes // 2)
    cluster2 = range(num_nodes // 2, num_nodes)
    G_final = nx.Graph()
    G_final.add_nodes_from(range(num_nodes))
    for i in cluster1:
        for j in cluster1:
            if i != j:
                G_final.add_edge(i, j)
    for i in cluster2:
        for j in cluster2:
            if i != j:
                G_final.add_edge(i, j)
    graphs.append(G_final)

    # 中間状態を補完
    for t in range(1, steps - 1):
        G_intermediate = nx.Graph()
        G_intermediate.add_nodes_from(range(num_nodes))
        for i in range(num_nodes):
            for j in range(i + 1, num_nodes):
                if (i in cluster1 and j in cluster1) or (i in cluster2 and j in cluster2):
                    G_intermediate.add_edge(i, j)
                elif np.random.rand() < (steps - t) / steps:
                    G_intermediate.add_edge(i, j)
        graphs.insert(-1, G_intermediate)

    return graphs



# 動的ネットワークの生成
dynamic_graphs = generate_dynamic_network(num_nodes=100, steps=100)
visualize_network(dynamic_graphs[0])  # 初期状態の可視化
visualize_network(dynamic_graphs[-1])  # 最終状態の可視化




In [34]:
import networkx as nx
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def visualize_snapshots_plotly(graph_snapshots, n_snapshots, layout='spring'):
    """
    Visualize static snapshots of a dynamic network using Plotly.

    Parameters:
        graph_snapshots (list of nx.Graph): List of graph snapshots.
        n_snapshots (int): Number of snapshots to display.
        layout (str): Graph layout type ('spring', 'circular', etc.).
    """
    # Select evenly spaced snapshots
    indices = np.linspace(0, len(graph_snapshots) - 1, n_snapshots, dtype=int)
    selected_snapshots = [graph_snapshots[i] for i in indices]

    # Create subplot grid
    cols = n_snapshots
    fig = make_subplots(rows=1, cols=cols, subplot_titles=[f"Snapshot {i+1}" for i in range(n_snapshots)])

    # Set layout function
    layout_func = nx.spring_layout if layout == 'spring' else nx.circular_layout

    # Generate plots for each snapshot
    for col, G in enumerate(selected_snapshots, start=1):
        pos = layout_func(G)
        x_nodes, y_nodes = zip(*[pos[node] for node in G.nodes()])
        edge_x = []
        edge_y = []
        for edge in G.edges():
            x0, y0 = pos[edge[0]]
            x1, y1 = pos[edge[1]]
            edge_x += [x0, x1, None]
            edge_y += [y0, y1, None]

        # Add edges
        fig.add_trace(
            go.Scatter(
                x=edge_x,
                y=edge_y,
                mode='lines',
                line=dict(color='gray', width=1),
                hoverinfo='none'
            ),
            row=1,
            col=col
        )

        # Add nodes
        fig.add_trace(
            go.Scatter(
                x=x_nodes,
                y=y_nodes,
                mode='markers+text',
                marker=dict(size=10, color='lightblue'),
                text=list(G.nodes),
                textposition="top center",
                hoverinfo='text'
            ),
            row=1,
            col=col
        )

    # Update layout
    fig.update_layout(
        showlegend=False,
        height=400,
        width=300 * n_snapshots,
        title="Dynamic Network Snapshots",
        title_x=0.5
    )
    fig.show()


In [35]:
visualize_snapshots_plotly(dynamic_graphs, n_snapshots=5, layout='spring')  # 5 snapshots with spring layout

In [100]:
# 上で生成したような動的ネットワークを受け取り、ベクトル化、正規化、PCAによる可視化を行う
def visualize_dynamic_network_pca(DG):
    """
    動的ネットワークデータをPCAにより2次元に圧縮し可視化する関数。

    Parameters:
        DG (list of networkx.Graph): 動的ネットワークデータ
    """
    # ノード数
    num_nodes = len(DG[0].nodes())
    timestep = len(DG)  
    

    # ノードのベクトル化100ノードなら10000次元のベクトル
    node_vectors = np.zeros((len(DG), num_nodes * num_nodes))
    for i, G in enumerate(DG):
        # print(f"Processing snapshot {i + 1}") 
        adj_matrix = nx.to_numpy_array(G)
        # print(f"shape of adj_matrix: {adj_matrix.shape}")
        node_vectors[i] = adj_matrix.flatten()
    

    # 正規化
    # row_norms = np.linalg.norm(data, axis=1, keepdims=True)
    # normalized_data = data / row_norms
    node_vectors = node_vectors / np.linalg.norm(node_vectors, axis=1, keepdims=True)

    # print(f"shape of node_vectors: {node_vectors.shape}")
    # PCAによる次元削減
    from sklearn.decomposition import PCA
    pca = PCA(n_components=2)
    node_vectors_pca = pca.fit_transform(node_vectors)
    # print(f"shape of node_vectors_pca: {node_vectors_pca.shape}")

    # 可視化
    # 20段階に色分けしたline
    import plotly.express as px
    colors = px.colors.qualitative.Plotly
    
    fig = go.Figure()
    divide = 10
    for i in range(divide):
        # 20分割したi番目の点群
        x = node_vectors_pca[i * timestep // divide:(i + 1) * timestep // divide, 0]
        y = node_vectors_pca[i * timestep // divide:(i + 1) * timestep // divide, 1]
        fig.add_trace(go.Scatter(x=x, y=y, mode='lines+markers', line=dict(color=colors[i]), marker=dict(size=10), name=f"Snapshot {i+1}"))
        
   
    fig.show()
    

In [99]:
import plotly.express as px

colors = px.colors.qualitative.Plotly
len(colors)

10

# 停留状態

In [37]:
import networkx as nx
import random
import plotly.graph_objects as go

# 初期クラスタ構造を持つグラフ生成
def create_initial_cluster(num_nodes, num_clusters, intra_cluster_prob):
    """
    初期クラスタ構造を持つグラフを生成。
    """
    G = nx.Graph()
    nodes_per_cluster = num_nodes // num_clusters
    for cluster in range(num_clusters):
        cluster_nodes = range(cluster * nodes_per_cluster, (cluster + 1) * nodes_per_cluster)
        for i in cluster_nodes:
            for j in cluster_nodes:
                if i != j and random.random() < intra_cluster_prob:
                    G.add_edge(i, j)
    return G

# 停留フェーズのネットワーク生成
def generate_stay_phase_network(base_graph, prob_add=0.05, prob_remove=0.05):
    """
    停留フェーズのネットワークを生成する。
    """
    G = base_graph.copy()
    nodes = list(G.nodes())

    # クラスタ内エッジの追加
    for _ in range(int(prob_add * len(nodes) ** 2)):
        node_a, node_b = random.sample(nodes, 2)
        if not G.has_edge(node_a, node_b):  # エッジが存在しなければ追加
            G.add_edge(node_a, node_b)

    # クラスタ内エッジの削除
    for edge in list(G.edges()):
        if random.random() < prob_remove:  # 確率に基づき削除
            G.remove_edge(*edge)

    return G

# 可視化のための関数
def visualize_static_network(G, title="Static Network"):
    pos = nx.spring_layout(G)  # ノードの配置
    edge_x = []
    edge_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        edge_x += [x0, x1, None]
        edge_y += [y0, y1, None]
    node_x, node_y = zip(*[pos[node] for node in G.nodes()])

    fig = go.Figure()
    # Add edges
    fig.add_trace(go.Scatter(x=edge_x, y=edge_y, mode='lines', line=dict(color='gray', width=1), hoverinfo='none'))
    # Add nodes
    fig.add_trace(go.Scatter(x=node_x, y=node_y, mode='markers', marker=dict(size=10, color='blue'), hoverinfo='text'))
    fig.update_layout(showlegend=False, title=title, title_x=0.5)
    fig.show()

# 遷移フェーズと停留フェーズを生成
def create_dynamic_network(num_nodes, num_clusters, intra_cluster_prob, prob_add, prob_remove, N_transition, N_stop):
    """
    動的ネットワークの作成（遷移フェーズ -> 停留フェーズ）。
    - N_transition: 遷移フェーズの長さ（スナップショット数）
    - N_stop: 停留フェーズの長さ（スナップショット数）
    """
    # 初期クラスタ構造
    initial_graph = create_initial_cluster(num_nodes, num_clusters, intra_cluster_prob)
    
    # 遷移フェーズ
    transition_graphs = [initial_graph.copy()]
    for i in range(1, N_transition):
        transition_graphs.append(generate_stay_phase_network(transition_graphs[i-1], prob_add, prob_remove))
    
    # 停留フェーズ
    stay_graphs = []
    for i in range(N_stop):
        stay_graphs.append(generate_stay_phase_network(transition_graphs[-1], prob_add, prob_remove))

    # 遷移フェーズ + 停留フェーズのネットワークを結合
    return transition_graphs + stay_graphs

# 動的ネットワークの可視化
def visualize_dynamic_networks(networks):
    for i, G in enumerate(networks):
        visualize_static_network(G, title=f"Snapshot {i+1}")

# パラメータの設定
num_nodes = 50
num_clusters = 2
intra_cluster_prob = 0.5
prob_add = 0.1
prob_remove = 0.1
N_transition = 100  # 遷移フェーズのスナップショット数
N_stop = 100        # 停留フェーズのスナップショット数

# 動的ネットワークの作成と可視化
dynamic_networks = create_dynamic_network(num_nodes, num_clusters, intra_cluster_prob, prob_add, prob_remove, N_transition, N_stop)
visualize_snapshots_plotly(dynamic_networks, n_snapshots=10, layout='spring')  # 5 snapshots with spring layout


In [83]:
# 動的ネットワークの可視化
visualize_dynamic_network_pca(dynamic_graphs)

ValueError: 
    Invalid value of type 'builtins.int' received for the 'color' property of scatter.line
        Received value: 0

    The 'color' property is a color and may be specified as:
      - A hex string (e.g. '#ff0000')
      - An rgb/rgba string (e.g. 'rgb(255,0,0)')
      - An hsl/hsla string (e.g. 'hsl(0,100%,50%)')
      - An hsv/hsva string (e.g. 'hsv(0,100%,100%)')
      - A named CSS color:
            aliceblue, antiquewhite, aqua, aquamarine, azure,
            beige, bisque, black, blanchedalmond, blue,
            blueviolet, brown, burlywood, cadetblue,
            chartreuse, chocolate, coral, cornflowerblue,
            cornsilk, crimson, cyan, darkblue, darkcyan,
            darkgoldenrod, darkgray, darkgrey, darkgreen,
            darkkhaki, darkmagenta, darkolivegreen, darkorange,
            darkorchid, darkred, darksalmon, darkseagreen,
            darkslateblue, darkslategray, darkslategrey,
            darkturquoise, darkviolet, deeppink, deepskyblue,
   

動的ネットワークのデータを生成します。
Newman, Watts, and Strogatz のスモールワールドモデルをもとに、安定なネットワークを4つ定義します。安定状態1は１つのクラスタ、2は2つのクラスタ、3は3つのクラスタ、4は一つのクラスタにします
それから、状態で125ステップ安定し、50ステップで別の状態に遷移するような動的ネットワークを生成してください。
安定状態では、クラスタ内のデータとのノードリンクの追加や削除が行われます。

In [75]:
import numpy as np
import networkx as nx
import plotly.graph_objects as go
from itertools import cycle
import random

# パラメータ設定
num_nodes = 100
p_rewire = 0.4
stable_steps = 125
transition_steps = 50
states = [1, 2, 3, 4]  # 安定状態

# 各状態のグラフを生成
def generate_network(state):
    if state == 1:
        return nx.watts_strogatz_graph(num_nodes, k=4, p=p_rewire)
    elif state == 2:
        G = nx.watts_strogatz_graph(num_nodes // 2, k=4, p=p_rewire)
        H = nx.watts_strogatz_graph(num_nodes // 2, k=4, p=p_rewire)
        G = nx.disjoint_union(G, H)
        return G
    elif state == 3:
        G = nx.watts_strogatz_graph(num_nodes // 3, k=4, p=p_rewire)
        H = nx.watts_strogatz_graph(num_nodes // 3, k=4, p=p_rewire)
        I = nx.watts_strogatz_graph(num_nodes // 3+1, k=4, p=p_rewire)
        G = nx.disjoint_union(G, H)
        G = nx.disjoint_union(G, I)
        return G
    elif state == 4:
        return nx.watts_strogatz_graph(num_nodes, k=4, p=p_rewire)

# 2つのネットワーク間の遷移を行う
def transition_network(G1, G2, step, max_steps):
    G = G1.copy()
    edges1 = set(G1.edges())
    edges2 = set(G2.edges())
    add_edges = list(edges2 - edges1)
    remove_edges = list(edges1 - edges2)
    
    num_add = int(len(add_edges) * (step / max_steps))
    num_remove = int(len(remove_edges) * (step / max_steps))
    
    for _ in range(num_add):
        if add_edges:
            edge = random.choice(add_edges)
            G.add_edge(*edge)
            add_edges.remove(edge)
    
    for _ in range(num_remove):
        if remove_edges:
            edge = random.choice(remove_edges)
            G.remove_edge(*edge)
            remove_edges.remove(edge)
    
    return G

# 動的ネットワークの生成
time_series = []
state_cycle = cycle(states)
current_state = next(state_cycle)
next_state = next(state_cycle)
steps = 0

while steps < 1000:  # 全体のステップ数
    if steps % (stable_steps + transition_steps) == 0:
        current_state = next_state
        next_state = next(state_cycle)
    
    if (steps % (stable_steps + transition_steps)) < stable_steps:
        G = generate_network(current_state)
    else:
        transition_step = (steps % (stable_steps + transition_steps)) - stable_steps
        G1 = generate_network(current_state)
        G2 = generate_network(next_state)
        G = transition_network(G1, G2, transition_step, transition_steps)
    
    time_series.append(G)
    steps += 1

G = time_series[-1]
print(len(time_series))
visualize_snapshots_plotly(time_series, n_snapshots=20, layout='spring')  # 5 snapshots with spring layout

1000


In [102]:
# save time_series
# ベクトル化、正規化をしたものを保存
import pickle
node_vectors = []
for G in time_series:
    adj_matrix = nx.to_numpy_array(G)
    node_vectors.append(adj_matrix.flatten())
node_vectors = np.array(node_vectors)
node_vectors = node_vectors / np.linalg.norm(node_vectors, axis=1, keepdims=True)
with open("time_series.pkl", "wb") as f:
    pickle.dump(node_vectors, f)

In [55]:
time_series[0]

In [101]:
#　隣接行列の取得

visualize_dynamic_network_pca(time_series)

In [40]:
import numpy as np
import networkx as nx
import plotly.graph_objects as go
def draw_network(adj_matrix):
    # NetworkX グラフの作成
    G = nx.from_numpy_array(adj_matrix)
    pos = nx.spring_layout(G)  # ノードの座標を決定

    # エッジの描画
    ego_x = []
    ego_y = []
    for edge in G.edges():
        x0, y0 = pos[edge[0]]
        x1, y1 = pos[edge[1]]
        ego_x.extend([x0, x1, None])
        ego_y.extend([y0, y1, None])

    edge_trace = go.Scatter(
        x=ego_x, y=ego_y,
        line=dict(width=1, color='black'),
        hoverinfo='none',
        mode='lines'
    )

    # ノードの描画
    node_x = []
    node_y = []
    for node in G.nodes():
        x, y = pos[node]
        node_x.append(x)
        node_y.append(y)

    node_trace = go.Scatter(
        x=node_x, y=node_y,
        mode='markers',
        marker=dict(size=10, color='blue'),
        text=[str(n) for n in G.nodes()],
        hoverinfo='text'
    )

    # プロットの作成
    fig = go.Figure(data=[edge_trace, node_trace])
    fig.update_layout(
        showlegend=False,
        margin=dict(b=0, l=0, r=0, t=0),
        xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
        yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)
    )
    fig.show()


In [41]:
file_path = "./../data/dynamic_network/evolution-graph-100-900-recurr.csv"
# ファイルの読み込み最初の行を無視して10000列900行を読み込む
adj_matrix = np.loadtxt(file_path, delimiter=',', skiprows=1)
n = 200
draw_network(adj_matrix[n].reshape(100, 100))

